In [1]:
# Exercise 3.1.1 Scrape using Selenium

from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions 

executable_path = '.\geckodriver'

In [6]:
import time

# Activate 2 drivers, one for restaurant page and the other one for review page
driver1 = webdriver.Firefox(executable_path=executable_path)
driver2 = webdriver.Firefox(executable_path=executable_path)

# Let driver1 load Hoboken restaurants
driver1.get('https://www.yelp.com/search?cflt=restaurants&find_loc=Hoboken%2C%20NJ')

csv_output_post_covid = []
csv_output_pre_covid = []

# the number of pages we want to scrap
for i in range(24):
    
    # wait for the content to be loaded
    time.sleep(5)   
    
    # load the links of restaurant and restaurant ratings
    restaurant_links = driver1.find_elements_by_css_selector("[class=\"css-1422juy\"]")
    rstnt_ratings = driver1.find_elements_by_css_selector("div.i-stars__09f24__foihJ")
    time.sleep(3) 
    print(len(restaurant_links))
    
    # we scrawl from 5th element because the first 2 are irrelevent buttons and the 3,4th and -1th are sponsored restaurants
    for j, link in enumerate(restaurant_links[4:-1]):
        
        # Extract link texts and rating labels
        restaurant_name = link.text
        rstnt_rating = rstnt_ratings[j].get_attribute('aria-label')
        print("restaurant_name and rstnt_rating", restaurant_name, rstnt_rating)
        
        # Extract link url label and let driver2 load it
        comment_link = link.get_attribute('href')
        driver2.get(comment_link)
        
        # Scrap the "more" button to find all ammenity information
        more = driver2.find_elements_by_css_selector("div[role=\" css-7onyyv\"] button[type=\"submit\"]")
        # if more not > 0, it means "Amenities and More" is having a small number so the "more" button does not apply here
        if len(more)>0:
            more[0].click()
        
        # collect "Amenities and More items" including ammenities included and not included
        time.sleep(3)
        ammeneties = ""
        ammeneties_and_more = driver2.find_elements_by_css_selector("section[aria-label=\"Amenities and More\"] span[class=\" css-oe5jd3\"]")
        # "Amenities and More" can be empty so we need to check it
        if len(ammeneties_and_more)>0:
            print(ammeneties_and_more[0].text)
            for a in ammeneties_and_more:
                ammeneties += a.text +"\n"
        time.sleep(3)
        Xammeneties = ""
        Xammeneties_and_more = driver2.find_elements_by_css_selector("section[aria-label=\"Amenities and More\"] span[class=\" css-v2vuco\"]")
        if len(Xammeneties_and_more)>0:
            print(Xammeneties_and_more[0].text)
            for a in Xammeneties_and_more:
                Xammeneties += a.text +"\n"
        
        # extract the maximum number of review pages, so we know how far we can loop through these pages
        time.sleep(5)
        max_page_tag = driver2.find_elements_by_css_selector("div.pagination__373c0__1mPhx span[class=\" css-wc5edd\"]")[0].text
        max_page = int(max_page_tag.split()[-1])
        
        # click the "sort" button and "newest first" button to make latest comments show on our page
        yelp_sort_button = driver2.find_elements_by_css_selector("button.css-s36a9t")
        yelp_sort_button[0].click()
        time.sleep(5)
        button_list = driver2.find_elements_by_css_selector("button.menu-item__373c0__18VDP")
        newest_first_button = button_list[1]
        newest_first_button.click()
        time.sleep(5) 
        
        # Specify the page number we want to scrap from restaurants. 
        rstnt_pages_to_scrap = 3
        for j in range(rstnt_pages_to_scrap):
            # Make sure the page index does not exceed the max page number or and error will pop up
            if j<max_page:
                # Extract review data including comment, rating and date
                comments = driver2.find_elements_by_css_selector("div.review__373c0__3MsBX span[lang=\"en\"]")
                cust_ratings = driver2.find_elements_by_css_selector("div.review__373c0__3MsBX div[role=\"img\"]")
                dates = driver2.find_elements_by_css_selector("div.review__373c0__3MsBX span[class=\" css-wc5edd\"]")
                print("page:", j)
                # The for-loop includes the comment and its correspnding information. We then append the info to output lists.
                for l, comment in enumerate(comments):
                    print("comment:", comment.text)
                    print("rating:", cust_ratings[l].get_attribute('aria-label'))
                    print("date:", dates[l].text)
                    csv_output_post_covid.append([comment.text, cust_ratings[l].get_attribute('aria-label'), dates[l].text, ammeneties, Xammeneties, restaurant_name, rstnt_rating])
                # The if statement again filters out exceeded page indices and we capture the next page number button
                if j<max_page-1:
                    next_rstnt_page = driver2.find_element_by_css_selector("[aria-label=\"Page: " + str(j+2) + "\"]")
                    next_rstnt_page.click()        
            else:
                break
            time.sleep(5)
        
        # click the "sort" button and "oldest first" button to make earliest comments show on our page
        yelp_sort_button = driver2.find_elements_by_css_selector("button.css-s36a9t")
        time.sleep(5)
        yelp_sort_button[0].click()
        time.sleep(5)
        button_list = driver2.find_elements_by_css_selector("button.menu-item__373c0__18VDP")
        oldest_first_button = button_list[2]
        oldest_first_button.click()
        time.sleep(5) 
        
        for j in range(rstnt_pages_to_scrap):
            if j<max_page:
                # Extract review data including comment, rating and date
                comments = driver2.find_elements_by_css_selector("div.review__373c0__3MsBX span[lang=\"en\"]")
                cust_ratings = driver2.find_elements_by_css_selector("div.review__373c0__3MsBX div[role=\"img\"]")
                dates = driver2.find_elements_by_css_selector("div.review__373c0__3MsBX span[class=\" css-wc5edd\"]")

                # The for-loop includes the comment and its correspnding information. We then append the info to output lists.
                for l, comment in enumerate(comments):

                    print("comment:", comment.text)
                    print("rating:", cust_ratings[l].get_attribute('aria-label'))
                    print("date:", dates[l].text)
                    csv_output_pre_covid.append([comment.text, cust_ratings[l].get_attribute('aria-label'), dates[l].text, ammeneties, Xammeneties, restaurant_name, rstnt_rating])
                
                if j!=max_page-1:
                    next_rstnt_page = driver2.find_element_by_css_selector("[aria-label=\"Page: " + str(j+2) + "\"]")
                    next_rstnt_page.click()
            else:
                break
            time.sleep(5)
            
        # -----------------
            
    # load the next page of restaurants in the region (Hoboken)
    next_page_link=driver1.find_element_by_css_selector("[aria-label=\"Page: " + str(i+2) + "\"]")
    print(next_page_link)
    next_page_link.click()

15
restaurant_name and rstnt_rating Grand Vin 3.5 star rating
Takes Reservations
page: 0
comment: Bartender tonight kept passing us by and waiting on customers who came in after us.  Sat there for 20 minutes and never even acknowledged us. I guess we weren't boujee enough.  Don't bother with this place unless rude staff and expensive average tasting food is your thing.  Portions were small
rating: 1 star rating
date: 11/19/2021
comment: This is a lovely neighborhood spot for brunch and dinner. The Caesar salad tacos and pastas are really delicious. The breakfast gnocchi was okay for brunch, but my boyfriend and mother loved the steak and eggs. Cocktails here are creative and tasty.
rating: 4 star rating
date: 11/18/2021
comment: I was trying to order pick up on a Friday night, after calling with no answer?!? Finally, they told me to call back at 9 o'clock. I waited two hours and didn't order from any other place expecting to order. I called back at 9 o'clock and they said they were too

rating: 5 star rating
date: 8/4/2021
comment: All in all we had a good time here ! The spot is beautiful - I love green and white floral decor personally. We came for a Saturday brunch and were seated with reservations outdoors. The prosecco sangria was tasty and the drink menu was extensive. I LOVED my smoked salmon toast which was delicious and huge for $7. I also liked the arugula salad. My friends enjoyed their entrees as well. Honestly, my only gripe is the service. We weren't server for 45 minutes. I had to ask a server if we could order bc we were starving and sweating outside lol The server later apologized saying no one was ever assigned to our table, which makes sense. We were literally forgotten. BUT, the food and drinks were great so I'd still recommend!
rating: 4 star rating
date: 7/31/2021
comment: Cute restaurant with intimate seating both inside snd out.  Recently attended a Baby Shower and everything was perfect from decor to food.  A clean and inviting interior that w

comment: Came down for a quick bite after a long day. We got a spot at the high table, between the bar and the restaurant. I'm 5'10", so not short, and I had to really stretch to get up on the bench and grab onto the very wobbly table to steady myself, this table is a hazard and could use with a step or something from the floor as to not knock over the flower vase.

So we ordered 2 glasses of wine and that came to ~ $30, it was a nice Pinot noir, but nothing to write home about and the pours were so small that it felt like quite a rip off.

We wanted to order some food, it was about 8:30pm and both the bartender and the server told us that the kitchen was slammed and we'd be better off not ordering food (new restaurant, still working out the kinks). This was disappointing, but we appreciated their honesty. The menu is massive, perhaps too massive and all of the food that did go by us seemed quite heavy on the sauce though, so this may have been for the best in the end.

We ordered dess

rating: 5 star rating
date: 3/8/2016
comment: I went on Friday night with a girlfriend for dinner. The restaurant has a great atmosphere. It reminded me of California wine country. The cocktail list was interesting. They had lots of different kinds of drinks. I'll have to try the brine next time (beer and wine mixed).

We shared two appetizers, a pasta dish and an entree and were stuffed. Favorites were the veal meatballs, chicken francaise and the gnocchi. The menu is varied so there is something for everyone.

The staff was attentive and special shout out to the owner Dan for checking up on us to ensure everything was great.

Can't wait to come back and try some other entrees and as well as the brunch, which the menu said was coming soon!
rating: 5 star rating
date: 3/8/2016
comment: The quality of food you remember from 3A's (former restaurant in this location), with the class this part of Hoboken needed. The atmosphere is gorgeous and plays into the the vintner theme without crossi

comment: I was very excited to try Grand Vin as there looked to finally be a great local food/drink spot to replace 3As. The interior is nice, good decor and vibe. However, the menu is fairly limited and overpriced. They do a good job on some dishes and others leave you quite underwhelmed. In general, the pastas are a safe choice (although $20 for rigatoni in a watery cream sauce is pricey). Steer clear of the Branzino with grilled vegetables. The dish comes with two thin filets (albeit nicely seasoned) and FIVE thin overcooked zucchini rounds. I had to ration each round into small bites to try and make it last through the meal -- no luck. There were no other sides on the plate, just the empty space staring back. The meal was $26. Same story with the Spiedino appetizer. GV's take on fried mozzarella. Be prepared to receive nothing more than a small grilled cheese sandwich battered and fried, served with a side of salty anchovy sauce. This dish was $12 for two pieces of white bread with

...

rating: 5 star rating
date: 2/9/2020
comment: I loveeee the gnocchi from here. The renovation looks great. The nice seating outside is my favorite for enjoying the weather and people watching.
rating: 5 star rating
date: 3/14/2020
comment: The food in this place is bomb. The pizza is great, all options. The buffalo wings as well. They have a wide variety of drinks as well (it's a bar with good food). Stop by if your in the area
rating: 5 star rating
date: 5/16/2020
comment: They play rap and the crowd doesn't suck.

The music was actually a decent mix and the DJ even took my request.

Place is cute, not huge but comfortable and good vibes.

Drinks seemed solid. Everyone seemed pretty wasted but there were no problems or fights which is always appreciated.
rating: 5 star rating
date: 3/11/2021
comment: "Bouncer" told me I could not go in wearing shorts. He said you need to pay 20 dollars to come in if you are wearing shorts. I told him i'll go elsewhere. Horrible service.
rating: 1 star

page: 2
comment: Easily the best bagels in Hoboken and perhaps including New York City area.  These are made in a classic style fresh daily... These are far superior to H&H bagels which seem like a big hype to me. ( although I do go to HH once in a while to compare; ehh) i've been coming to Hobo bagels for years...(20). It's a small hole in the wall type of shop with a quirky Small town feeling. It's mostly take out with a couple of seats upfront. Classic selection of flavors... You can't go wrong with whatever you want to put on it or just eating and playing.
rating: 5 star rating
date: 5/2/2020
comment: I've been coming here for over 10 years and their bagels for me are by far the best. There are some bagel shops in New York that compete, but I think this place is superior. Their bagels have a great consistency to them with a nice balance of chew and nice outside. It is not this big airy tasteless fluff ball like up the block. It's a small place so it does get busy but all the other 

rating: 5 star rating
date: 7/12/2009
comment: the best bagel joint in Hoboken!

great variety and price. good selection of teas and juice as well.

their sausage/egg/cheese on a bagel is an extremely viable contender against the Dunkin Donuts sausage/egg/cheese on a croisssant.
rating: 4 star rating
date: 7/15/2009
comment: Crowded, tiny, noisy and smelling delicious - this is how bagel shops are supposed to be.  My BF had a bacon and egg on an everything bagel and just about swallowed it in three big bites (he was hungry, and it was good).  I tried the bagel holes and wished I had bought more. Never had a bagel hole before (just like a donute hole) and it was cute and bitesize which was exactly what I was looking for before a big day out.
rating: 4 star rating
date: 9/7/2009
comment: This is the closest bagel place to my apartment, and it's always busy.  The bagels are delicious and if to go early in the morning, they're still hot out of the oven!
rating: 5 star rating
date: 1/24/201

restaurant_name and rstnt_rating Dino & Harrys Steak House 3.5 star rating


IndexError: list index out of range

In [7]:
import pandas as pd

corpus_rating = pd.DataFrame(csv_output_pre_covid)
new_column_names = ['Comment', 'Rating', 'date', 'ammenity', 'ammenity not included', 'restaurant', 'restaurant rating']
corpus_rating.to_csv('corpus_rating_precovid6.csv', index=False, header=new_column_names)

corpus_rating = pd.DataFrame(csv_output_post_covid)
new_column_names = ['Comment', 'Rating', 'date', 'ammenity', 'ammenity not included', 'restaurant', 'restaurant rating']
corpus_rating.to_csv('corpus_rating_postcovid6.csv', index=False, header=new_column_names)